In [ ]:
import os
import pprint
import tempfile

from typing import Dict, Text

import numpy as np
import tensorflow as tf
import tensorflow_datasets as tfds

import tensorflow as tf
import numpy as np
import pandas as pd

In [2]:
dataframe = pd.read_csv("Product data.csv")

dataframe = dataframe.iloc[:100000,:]

In [3]:
dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 8 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   Unnamed: 0  100000 non-null  int64  
 1   userId      100000 non-null  int64  
 2   movieId     100000 non-null  int64  
 3   rating      100000 non-null  float64
 4   timestamp   100000 non-null  object 
 5   title       100000 non-null  object 
 6   genres      100000 non-null  object 
 7   Overview    100000 non-null  object 
dtypes: float64(1), int64(3), object(4)
memory usage: 6.1+ MB


In [4]:
dataframe = dataframe[['userId','movieId','title']]

In [5]:
# dataframe['userId'].astype(np.int32)
# dataframe['movieId'].astype(np.int32)

In [6]:
dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 3 columns):
 #   Column   Non-Null Count   Dtype 
---  ------   --------------   ----- 
 0   userId   100000 non-null  int64 
 1   movieId  100000 non-null  int64 
 2   title    100000 non-null  object
dtypes: int64(2), object(1)
memory usage: 2.3+ MB


In [7]:
# ratings =dataframe[['userId','title']]
# movies = dataframe['title']

In [8]:
def dataframe_to_dataset(dataframe):
    dataframe = dataframe.copy()
   #labels = dataframe.pop("POLICY_STATUS")
    ds = tf.data.Dataset.from_tensor_slices((dict(dataframe)))
    ds = ds.shuffle(buffer_size=len(dataframe))
    return ds


dataframe_ds = dataframe_to_dataset(dataframe)
#movies_ds = dataframe_to_dataset(movies)

In [9]:
dataframe_ds

<_ShuffleDataset element_spec={'userId': TensorSpec(shape=(), dtype=tf.int64, name=None), 'movieId': TensorSpec(shape=(), dtype=tf.int64, name=None), 'title': TensorSpec(shape=(), dtype=tf.string, name=None)}>

In [10]:
# Shuffle the data
#dataframe_ds = dataframe_to_dataset(dataframe)
dataframe_ds = dataframe_ds.shuffle(len(dataframe), reshuffle_each_iteration=False)

In [11]:
# Split the data into train and test with 80/20 split
train_size = int(0.8 * len(dataframe))
train_ds = dataframe_ds.take(train_size)
test_ds = dataframe_ds.skip(train_size)

In [12]:
# Creating the train and test datasets
ratings_train = train_ds.map(lambda x: {
    "title": x["title"],
    "userId": tf.strings.as_string(x["userId"]),
})

ratings_test = test_ds.map(lambda x: {
    "title": x["title"],
    "userId": tf.strings.as_string(x["userId"]),
})

movies_train = train_ds.map(lambda x: x["title"])
movies_test = test_ds.map(lambda x: x["title"])

In [13]:
# ratings = dataframe_ds.map(lambda x: {
#     "movie_title": x["title"],
#     "user_id": x["userId"],
# })
# movies = dataframe_ds.map(lambda x: x["title"])

In [67]:
for x in ratings_train.take(1).as_numpy_iterator():
  pprint.pprint(x)

{'title': b'Pulp Fiction', 'userId': b'52644'}


In [15]:
for x in movies_train.take(1).as_numpy_iterator():
  pprint.pprint(x)

b'Clerks'


In [16]:
user_ids = dataframe_ds.batch(1_000_000).map(lambda x: x["userId"])
unique_user_ids = np.unique(np.concatenate(list(user_ids)))
unique_user_ids[:10]

array([ 1,  3,  8, 11, 13, 15, 16, 18, 21, 22], dtype=int64)

In [17]:
unique_user_idss = unique_user_ids.astype(str)

In [18]:
unique_user_ids = unique_user_idss.astype(object)

In [19]:
unique_user_ids[:10]

array(['1', '3', '8', '11', '13', '15', '16', '18', '21', '22'],
      dtype=object)

In [20]:
movie_titles = dataframe_ds.batch(1_000).map(lambda x: x["title"])
unique_movie_titles = np.unique(np.concatenate(list(movie_titles)))
unique_movie_titles[:10]

array([b'Clerks', b'Pulp Fiction', b"What's Eating Gilbert Grape"],
      dtype=object)

In [21]:
embedding_dimension =32

In [22]:
#unique_user_ids = [str(uid) for uid in unique_user_ids]

In [23]:
#unique_user_ids = np.array(unique_user_ids, dtype=object)

In [24]:
#unique_user_ids

In [25]:
user_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_ids, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_ids) + 1, embedding_dimension)
])

The canditate tower

In [26]:
movie_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_movie_titles, mask_token=None),
  tf.keras.layers.Embedding(len(unique_movie_titles) + 1, embedding_dimension)
])

Metrics

In [27]:
#pip install tensorflow-recommenders

In [28]:
import tensorflow_recommenders as tfrs

In [29]:
metrics = tfrs.metrics.FactorizedTopK(
  candidates=movies_train.batch(128).map(movie_model)
)

In [30]:
task = tfrs.tasks.Retrieval(
  metrics=metrics
)

**The Full Model**

In [31]:
class MovielensModel(tfrs.Model):

  def __init__(self, user_model, movie_model):
    super().__init__()
    self.movie_model: tf.keras.Model = movie_model
    self.user_model: tf.keras.Model = user_model
    self.task: tf.keras.layers.Layer = task

  def compute_loss(self, features: Dict[Text, tf.Tensor], training=False) -> tf.Tensor:
    # We pick out the user features and pass them into the user model.
    user_embeddings = self.user_model(features["userId"])
    # And pick out the movie features and pass them into the movie model,
    # getting embeddings back.
    positive_movie_embeddings = self.movie_model(features["title"])

    # The task computes the loss and the metrics.
    return self.task(user_embeddings, positive_movie_embeddings)

In [32]:
class NoBaseClassMovielensModel(tf.keras.Model):

  def __init__(self, user_model, movie_model):
    super().__init__()
    self.movie_model: tf.keras.Model = movie_model
    self.user_model: tf.keras.Model = user_model
    self.task: tf.keras.layers.Layer = task

  def train_step(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:

    # Set up a gradient tape to record gradients.
    with tf.GradientTape() as tape:

      # Loss computation.
      user_embeddings = self.user_model(features["userId"])
      positive_movie_embeddings = self.movie_model(features["title"])
      loss = self.task(user_embeddings, positive_movie_embeddings)

      # Handle regularization losses as well.
      regularization_loss = sum(self.losses)

      total_loss = loss + regularization_loss

    gradients = tape.gradient(total_loss, self.trainable_variables)
    self.optimizer.apply_gradients(zip(gradients, self.trainable_variables))

    metrics = {metric.name: metric.result() for metric in self.metrics}
    metrics["loss"] = loss
    metrics["regularization_loss"] = regularization_loss
    metrics["total_loss"] = total_loss

    return metrics

  def test_step(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:

    # Loss computation.
    user_embeddings = self.user_model(features["userId"])
    positive_movie_embeddings = self.movie_model(features["title"])
    loss = self.task(user_embeddings, positive_movie_embeddings)

    # Handle regularization losses as well.
    regularization_loss = sum(self.losses)

    total_loss = loss + regularization_loss

    metrics = {metric.name: metric.result() for metric in self.metrics}
    metrics["loss"] = loss
    metrics["regularization_loss"] = regularization_loss
    metrics["total_loss"] = total_loss

    return metrics

In [33]:
# Model configuration
model = MovielensModel(user_model, movie_model)
model.compile(optimizer=tf.keras.optimizers.Adagrad(learning_rate=0.1))

In [34]:
# Training the model
cached_train = ratings_train.batch(8192).cache()
model.fit(cached_train, epochs=2)


Epoch 1/2
10/10 [==============================] - 118s 12s/step - factorized_top_k/top_1_categorical_accuracy: 0.1743 - factorized_top_k/top_5_categorical_accuracy: 0.1743 - factorized_top_k/top_10_categorical_accuracy: 0.1743 - factorized_top_k/top_50_categorical_accuracy: 0.1743 - factorized_top_k/top_100_categorical_accuracy: 0.1743 - loss: 70372.2294 - regularization_loss: 0.0000e+00 - total_loss: 70372.2294
Epoch 2/2
10/10 [==============================] - 115s 12s/step - factorized_top_k/top_1_categorical_accuracy: 0.0320 - factorized_top_k/top_5_categorical_accuracy: 0.0320 - factorized_top_k/top_10_categorical_accuracy: 0.0320 - factorized_top_k/top_50_categorical_accuracy: 0.0320 - factorized_top_k/top_100_categorical_accuracy: 0.0320 - loss: 70621.3388 - regularization_loss: 0.0000e+00 - total_loss: 70621.3388


In [35]:
# Evaluating the model
cached_test = ratings_test.batch(4096).cache()
results = model.evaluate(cached_test)

print("Loss: ", results[0])
for name, value in zip(model.metrics_names[1:], results[1:]):
    print(name, ": ", value)


5/5 [==============================] - 36s 7s/step - factorized_top_k/top_1_categorical_accuracy: 0.3143 - factorized_top_k/top_5_categorical_accuracy: 0.3143 - factorized_top_k/top_10_categorical_accuracy: 0.3143 - factorized_top_k/top_50_categorical_accuracy: 0.3143 - factorized_top_k/top_100_categorical_accuracy: 0.3143 - loss: 32550.3294 - regularization_loss: 0.0000e+00 - total_loss: 32550.3294
Loss:  0.314300000667572
factorized_top_k/top_5_categorical_accuracy :  0.314300000667572
factorized_top_k/top_10_categorical_accuracy :  0.314300000667572
factorized_top_k/top_50_categorical_accuracy :  0.314300000667572
factorized_top_k/top_100_categorical_accuracy :  0.314300000667572


# Making predictions

In [61]:
movies_combined = tf.data.Dataset.concatenate(movies_train, movies_test)

In [70]:
ratings_combined = tf.data.Dataset.concatenate(ratings_train, ratings_test)

In [62]:
# Create a model that takes in raw query features, and
index = tfrs.layers.factorized_top_k.BruteForce(model.user_model)
# recommends movies out of the entire movies dataset.
index.index_from_dataset(
  tf.data.Dataset.zip((movies_combined.batch(100), movies_combined.batch(100).map(model.movie_model)))
)

# Get recommendations.
_, titles = index(tf.constant(["42"]))
print(f"Recommendations for user 42: {titles[0, :5]}")

Recommendations for user 42: [b"What's Eating Gilbert Grape" b'Pulp Fiction' b'Pulp Fiction' b'Clerks'
 b'Clerks']


In [65]:
for user_id in unique_user_ids:
    _, titles = index(tf.constant([user_id]))
    print(f"Recommendations for user {user_id}: {titles[0, :100]}")


Recommendations for user 1: [b"What's Eating Gilbert Grape" b'Pulp Fiction' b'Pulp Fiction' b'Clerks'
 b'Clerks' b'Clerks' b'Pulp Fiction' b'Clerks'
 b"What's Eating Gilbert Grape" b'Clerks']
Recommendations for user 3: [b'Pulp Fiction' b'Clerks' b'Pulp Fiction' b'Pulp Fiction' b'Pulp Fiction'
 b'Pulp Fiction' b'Clerks' b'Clerks' b'Pulp Fiction' b'Pulp Fiction']
Recommendations for user 8: [b'Pulp Fiction' b'Clerks' b"What's Eating Gilbert Grape"
 b"What's Eating Gilbert Grape" b'Pulp Fiction' b'Pulp Fiction'
 b'Pulp Fiction' b'Pulp Fiction' b'Clerks' b'Clerks']
Recommendations for user 11: [b'Pulp Fiction' b'Clerks' b"What's Eating Gilbert Grape"
 b"What's Eating Gilbert Grape" b'Pulp Fiction' b'Pulp Fiction'
 b'Pulp Fiction' b'Pulp Fiction' b'Clerks' b'Clerks']
Recommendations for user 13: [b'Pulp Fiction' b'Clerks' b'Pulp Fiction' b'Pulp Fiction' b'Pulp Fiction'
 b'Pulp Fiction' b'Clerks' b'Clerks' b'Pulp Fiction' b'Pulp Fiction']
Recommendations for user 15: [b'Pulp Fiction' b'Cler

KeyboardInterrupt: 

In [76]:
recommendations_dict = {}

for user_id in unique_user_ids[:20]:
    _, titles = index(tf.constant([user_id]))
    recommendations = titles[0, :5].numpy().tolist()
    recommendations_dict[user_id] = recommendations

print(recommendations_dict)

{'1': [b"What's Eating Gilbert Grape", b'Pulp Fiction', b'Pulp Fiction', b'Clerks', b'Clerks'], '3': [b'Pulp Fiction', b'Clerks', b'Pulp Fiction', b'Pulp Fiction', b'Pulp Fiction']}


In [74]:
relevance_dict = {}

for user_id in unique_user_ids[:20]:
    _, titles = index(tf.constant([user_id]))
    top_titles = titles[0, :5].numpy().tolist()

    relevance_dict[user_id] = {}

    for title in top_titles:
        relevance_dict[user_id][title] = int(title in list(ratings_combined.map(lambda x: x["title"]).as_numpy_iterator()))

print(relevance_dict)


{'1': {b"What's Eating Gilbert Grape": 1, b'Pulp Fiction': 1, b'Clerks': 1}, '3': {b'Pulp Fiction': 1, b'Clerks': 1}}


In [77]:
def calculate_precision(recommendations, relevance_labels):
    # Calculate precision for a single user
    # recommendations: List of recommended item IDs
    # relevance_labels: List of relevance labels corresponding to the items

    # Calculate the number of recommended items that are relevant (true positives)
    true_positives = sum(relevance_labels[item] for item in recommendations if item in relevance_labels)

    # Calculate precision
    precision = true_positives / len(recommendations)
    
    return precision


def calculate_average_precision(recommendations_dict, relevance_dict):
    # Calculate average precision across all users
    # recommendations_dict: Dictionary with user IDs as keys and recommended item IDs as values
    # relevance_dict: Dictionary with user IDs as keys and relevance labels as values

    total_precision = 0.0
    num_users = len(recommendations_dict)

    for user_id, recommendations in recommendations_dict.items():
        relevance_labels = relevance_dict[user_id]

        # Calculate precision for each user
        precision = calculate_precision(recommendations, relevance_labels)

        # Accumulate precision values
        total_precision += precision

    # Calculate average precision
    average_precision = total_precision / num_users

    return average_precision


# # Example usage

# # Assuming you have recommendations and relevance labels in the following format:
# recommendations_dict = {
#     'user1': ['item1', 'item2', 'item3'],
#     'user2': ['item2', 'item4', 'item5', 'item6'],
#     # ...
# }

# relevance_dict = {
#     'user1': {'item1': 1, 'item2': 1, 'item3': 0},
#     'user2': {'item2': 1, 'item4': 0, 'item5': 0, 'item6': 1},
#     # ...
# }

# Calculate average precision
average_precision = calculate_average_precision(recommendations_dict, relevance_dict)

# Print the average precision
print("Average Precision:", average_precision)


Average Precision: 1.0


In [78]:
def calculate_recall(recommendations, relevance_labels):
    # Calculate recall for a single user
    # recommendations: List of recommended item IDs
    # relevance_labels: Dictionary with item IDs as keys and relevance labels as values

    # Calculate the number of relevant items
    num_relevant_items = sum(relevance_labels[item] for item in relevance_labels)

    # Calculate the number of recommended items that are relevant (true positives)
    true_positives = sum(relevance_labels[item] for item in recommendations if item in relevance_labels)

    # Calculate recall
    recall = true_positives / num_relevant_items if num_relevant_items > 0 else 0.0

    return recall


def calculate_accuracy(recommendations_dict, relevance_dict):
    # Calculate accuracy across all users
    # recommendations_dict: Dictionary with user IDs as keys and recommended item IDs as values
    # relevance_dict: Dictionary with user IDs as keys and relevance labels as values

    total_recall = 0.0
    total_accuracy = 0.0
    num_users = len(recommendations_dict)

    for user_id, recommendations in recommendations_dict.items():
        relevance_labels = relevance_dict[user_id]

        # Calculate recall for each user
        recall = calculate_recall(recommendations, relevance_labels)

        # Calculate accuracy for each user
        accuracy = sum(relevance_labels[item] for item in recommendations if item in relevance_labels) / len(recommendations)

        # Accumulate recall and accuracy values
        total_recall += recall
        total_accuracy += accuracy

    # Calculate average recall and accuracy
    average_recall = total_recall / num_users
    average_accuracy = total_accuracy / num_users

    return average_recall, average_accuracy

# Calculate average recall and accuracy
average_recall, average_accuracy = calculate_accuracy(recommendations_dict, relevance_dict)

# Print the average recall and accuracy
#print("Average Recall:", average_recall)
print("Average Accuracy:", average_accuracy)


Average Recall: 2.0833333333333335
Average Accuracy: 1.0


In [79]:
def calculate_hit_ratio(recommendations_dict, relevance_dict):
    # Calculate hit ratio across all users
    # recommendations_dict: Dictionary with user IDs as keys and recommended item IDs as values
    # relevance_dict: Dictionary with user IDs as keys and relevance labels as values

    total_hit_ratio = 0.0
    num_users = len(recommendations_dict)

    for user_id, recommendations in recommendations_dict.items():
        relevance_labels = relevance_dict[user_id]

        # Check if any of the recommended items are relevant
        hits = any(relevance_labels[item] for item in recommendations)

        # Increment hit count if at least one recommendation is relevant
        hit_ratio = 1.0 if hits else 0.0

        # Accumulate hit ratio values
        total_hit_ratio += hit_ratio

    # Calculate average hit ratio
    average_hit_ratio = total_hit_ratio / num_users

    return average_hit_ratio


# Calculate average hit ratio
average_hit_ratio = calculate_hit_ratio(recommendations_dict, relevance_dict)

# Print the average hit ratio
print("Average Hit Ratio:", average_hit_ratio)


Average Hit Ratio: 1.0


In [80]:
def calculate_exact_sequence_hit_ratio(recommendations_dict, relevance_dict):
    # Calculate exact sequence hit ratio across all users
    # recommendations_dict: Dictionary with user IDs as keys and recommended item IDs as values
    # relevance_dict: Dictionary with user IDs as keys and relevance labels as values

    total_exact_sequence_hit_ratio = 0.0
    num_users = len(recommendations_dict)

    for user_id, recommendations in recommendations_dict.items():
        relevance_labels = relevance_dict[user_id]

        # Check if the recommended items match the relevant items exactly in sequence
        exact_sequence_hit = recommendations == list(relevance_labels.keys())

        # Increment hit count if the recommended items match exactly in sequence
        exact_sequence_hit_ratio = 1.0 if exact_sequence_hit else 0.0

        # Accumulate exact sequence hit ratio values
        total_exact_sequence_hit_ratio += exact_sequence_hit_ratio

    # Calculate average exact sequence hit ratio
    average_exact_sequence_hit_ratio = total_exact_sequence_hit_ratio / num_users

    return average_exact_sequence_hit_ratio


# Calculate average exact sequence hit ratio
average_exact_sequence_hit_ratio = calculate_exact_sequence_hit_ratio(recommendations_dict, relevance_dict)

# Print the average exact sequence hit ratio
print("Average Exact Sequence Hit Ratio:", average_exact_sequence_hit_ratio)


Average Exact Sequence Hit Ratio: 0.0


In [81]:
import numpy as np

def calculate_dcg(relevance_labels, k):
    # Calculate Discounted Cumulative Gain (DCG) at position k
    # relevance_labels: List of relevance labels
    # k: Position

    dcg = relevance_labels[0]
    for i in range(1, min(k, len(relevance_labels))):
        dcg += relevance_labels[i] / np.log2(i + 1)

    return dcg


def calculate_ndcg(recommendations_dict, relevance_dict, k):
    # Calculate Normalized Discounted Cumulative Gain (NDCG) across all users
    # recommendations_dict: Dictionary with user IDs as keys and recommended item IDs as values
    # relevance_dict: Dictionary with user IDs as keys and relevance labels as values
    # k: Position

    total_ndcg = 0.0
    num_users = len(recommendations_dict)

    for user_id, recommendations in recommendations_dict.items():
        relevance_labels = list(relevance_dict[user_id].values())

        # Calculate Discounted Cumulative Gain (DCG) at position k
        dcg = calculate_dcg(relevance_labels, k)

        # Sort relevance labels in descending order to calculate Ideal Discounted Cumulative Gain (IDCG)
        ideal_relevance_labels = sorted(relevance_labels, reverse=True)

        # Calculate Ideal Discounted Cumulative Gain (IDCG) at position k
        idcg = calculate_dcg(ideal_relevance_labels, k)

        # Calculate Normalized Discounted Cumulative Gain (NDCG)
        ndcg = dcg / idcg if idcg > 0 else 0.0

        # Accumulate NDCG values
        total_ndcg += ndcg

    # Calculate average NDCG
    average_ndcg = total_ndcg / num_users

    return average_ndcg


# Set the position at which to calculate NDCG
k = 5

# Calculate average NDCG at position k
average_ndcg = calculate_ndcg(recommendations_dict, relevance_dict, k)

# Print the average NDCG
print(f"Average NDCG@{k}: {average_ndcg}")


Average NDCG@5: 1.0
